In [1]:
!pip install duckdb
!pip install rdkit


In [2]:
import pandas as pd
import numpy as np
import duckdb

from pathlib import Path

In [9]:
TRAIN_CSV = Path('../data/raw/train.csv')
TEST_CSV = Path('../data/raw/test.csv')
TRAIN_PAR = Path('../data/raw/train.parquet')
TEST_PAR = Path('../data/raw/test.parquet')

con = duckdb.connect()

In [10]:
df_6e5 = con.query(f"""(SELECT *
                        FROM parquet_scan('{TRAIN_PAR}')
                        WHERE binds = 0
                        ORDER BY random()
                        LIMIT 30000)
                        UNION ALL
                        (SELECT *
                        FROM parquet_scan('{TRAIN_PAR}')
                        WHERE binds = 1
                        ORDER BY random()
                        LIMIT 30000)""").df()

df_5 = con.query(f"""(SELECT *
                        FROM parquet_scan('{TRAIN_PAR}')
                        LIMIT 5)""").df()

# con.close()

FloatProgress(value=0.0, layout=Layout(width='auto'), style=ProgressStyle(bar_color='black'))

In [12]:
df_dup_binds = con.query(f"""SELECT molecule_smiles, COUNT(*) as count
                                FROM parquet_scan('{TRAIN_PAR}')
                                WHERE binds = 1
                                GROUP BY molecule_smiles
                                HAVING COUNT(*) > 1
                                """).df()

In [21]:
print( df_dup_binds['count'].value_counts())

count
2    80003
3       62
Name: count, dtype: int64


In [17]:
df_dup_binds.head()

molecule_smiles  count
0  C#CC[C@@H](Nc1nc(Nc2cncc(C(=O)OC)c2)nc(Nc2n[nH...      2
1  C#CC[C@@H](Nc1nc(NCc2cncn2C)nc(Nc2cncc(OC)n2)n...      2
2  C#CC[C@@H](Nc1nc(NCC=Cc2cccnc2)nc(Nc2cncc(OC)n...      2
3  C#CC[C@@H](Nc1nc(NCc2cncc(F)c2)nc(Nc2ccsc2C(=O...      2
4  C#CC[C@@H](Nc1nc(NCc2cncc(F)c2)nc(Nc2sc(C)c(C)...      2

In [ ]:
from rdkit import Chem
from rdkit.Chem import AllChem
from sklearn.ensemble import RandomForestClassifier
from sklearn.model_selection import train_test_split
from sklearn.metrics import average_precision_score
from sklearn.preprocessing import OneHotEncoder

# Convert SMILES to RDKit molecules
df['molecule'] = df['molecule_smiles'].apply(Chem.MolFromSmiles)

# Generate ECFPs
def generate_ecfp(molecule, radius=2, bits=1024):
    if molecule is None:
        return None
    return list(AllChem.GetMorganFingerprintAsBitVect(molecule, radius, nBits=bits))

df['ecfp'] = df['molecule'].apply(generate_ecfp)

[12:18:17] DEPRECATION WARNING: please use MorganGenerator
[12:18:17] DEPRECATION WARNING: please use MorganGenerator
[12:18:17] DEPRECATION WARNING: please use MorganGenerator
[12:18:17] DEPRECATION WARNING: please use MorganGenerator
[12:18:17] DEPRECATION WARNING: please use MorganGenerator
[12:18:17] DEPRECATION WARNING: please use MorganGenerator
[12:18:17] DEPRECATION WARNING: please use MorganGenerator
[12:18:17] DEPRECATION WARNING: please use MorganGenerator
[12:18:17] DEPRECATION WARNING: please use MorganGenerator
[12:18:17] DEPRECATION WARNING: please use MorganGenerator
[12:18:17] DEPRECATION WARNING: please use MorganGenerator
[12:18:17] DEPRECATION WARNING: please use MorganGenerator
[12:18:17] DEPRECATION WARNING: please use MorganGenerator
[12:18:17] DEPRECATION WARNING: please use MorganGenerator
[12:18:17] DEPRECATION WARNING: please use MorganGenerator
[12:18:17] DEPRECATION WARNING: please use MorganGenerator
[12:18:17] DEPRECATION WARNING: please use MorganGenerat